In [1]:
from htmd.ui import *


2024-04-23 13:34:54,822 - numexpr.utils - INFO - NumExpr defaulting to 8 threads.


Registration is not approved: <html>
<head><title>405 Not Allowed</title></head>
<body>
<center><h1>405 Not Allowed</h1></center>
<hr><center>openresty</center>
</body>
</html>

Academic License 
HTMD Software Academic License Agreement v1.1

The HTMD software ("Software") has been developed by the contributing
researchers from Acellera and made available through Acellera for your
internal, non-profit research use.

Acellera allows researchers at your institution to run, display, copy and
modify Software on the following conditions:

1. The Software remains at your institution and is not published, distributed,
or otherwise transferred or made available to other than institution employees
and students involved in research under your supervision.

2. You agree to make results generated using Software available to other
academic researchers for non-profit research purposes. If you wish to obtain
Software for any commercial purposes, including fee-based service projects, you
will need to 

2024-04-23 13:35:06,347 - binstar - INFO - Using Anaconda API: https://api.anaconda.org


TypeError: can only join an iterable

In [3]:
from moleculekit.molecule import Molecule
from moleculekit.tools.voxeldescriptors import getVoxelDescriptors
from moleculekit.tools.atomtyper import prepareProteinForAtomtyping

# First let's read our two favourite protein and ligand structures
prot = Molecule( '3PTB')

prot.filter('protein')

prot = prepareProteinForAtomtyping(prot)
prot_vox, prot_centers, prot_N = getVoxelDescriptors(prot, buffer=8)

2024-04-22 14:39:10,911 - moleculekit.molecule - INFO - Removed 72 atoms. 1629 atoms remaining in the molecule.


NameError: name 'chain_id' is not defined

In [7]:
prot_vox.shape
features = prot_vox.reshape(prot_N[0], prot_N[1], prot_N[2], prot_vox.shape[1])
prot_vox.shape

(228872, 8)

In [6]:
for i in prot_vox:
    for ii in i:
        if ii != 0:
            print(ii)

1.1796882662951091e-06
1.1796882662951091e-06
1.1796882662951091e-06
1.248644147633371e-06
1.248644147633371e-06
1.248644147633371e-06
8.00669967215839e-07
8.00669967215839e-07
8.00669967215839e-07
1.1429134341156555e-06
1.1429134341156555e-06
1.1429134341156555e-06
1.209356300213571e-06
1.209356300213571e-06
1.209356300213571e-06
3.117518599049518e-06
3.117518599049518e-06
3.91044016123665e-06
3.91044016123665e-06
2.945322434055875e-06
2.945322434055875e-06
3.219805104426321e-06
3.219805104426321e-06
4.043778388695962e-06
4.043778388695962e-06
3.0410312247264315e-06
3.0410312247264315e-06
2.5236863883115745e-06
2.5236863883115745e-06
1.3711938047222816e-06
1.3711938047222816e-06
1.3711938047222816e-06
2.5359754877163354e-06
2.5359754877163354e-06
2.5359754877163354e-06
2.7051481747975004e-06
2.7051481747975004e-06
2.7051481747975004e-06
1.6358765532187292e-06
1.6358765532187292e-06
1.6358765532187292e-06
6.779489190034127e-07
6.779489190034127e-07
6.779489190034127e-07
1.2533538817915

In [3]:
import csv
import numpy as np
import os
from moleculekit.tools.atomtyper import metal_atypes
from moleculekit.molecule import Molecule
from moleculekit.tools.voxeldescriptors import getVoxelDescriptors
from moleculekit.tools.atomtyper import prepareProteinForAtomtyping

for file in ['data/ADP_Training.txt', 'data/ADP_Test.txt']:
    with open(file, newline='') as csvfile:

        reader = csv.reader(csvfile, delimiter=';')

        for row in reader:
            pdb_id = row[0]
            chain_id = row[1]

            if os.path.isfile(f'data/voxel-features/{pdb_id.lower()}{chain_id.upper()}.npy') \
                and os.path.isfile(f'data/voxel-annotations/{pdb_id.lower()}{chain_id.upper()}.npy'):
                continue
            print(pdb_id)
            binding_residues = [residue[1:] for residue in row[4].split(' ')]

            # selection query of the binding residues
            binding_residues_query = f'resid {" or resid ".join(binding_residues)}'

            if pdb_id == '3N3O':
                prot = Molecule('5SXR', validateElements=False)
            elif pdb_id == '1WE3':
                prot = Molecule('4V4O', validateElements=False)
            elif pdb_id == '3BFN':
                prot = Molecule('6NJE', validateElements=False)
            elif pdb_id == '3RBO':
                prot = Molecule('4JJZ', validateElements=False)
            elif pdb_id == '3QOV':
                prot = Molecule('4RVN', validateElements=False)
            else:
                prot = Molecule(pdb_id, validateElements=False)

            prot.filter(f'chain {chain_id} and protein')

            prot = prepareProteinForAtomtyping(prot)
            
            prot.filter(f"protein or water or element {' '.join(metal_atypes)}")

            prot_voxels, prot_centers, N = getVoxelDescriptors(prot, buffer=8)
            annotation_voxels, _, _ = getVoxelDescriptors(prot, buffer=8, userchannels=prot.atomselect(binding_residues_query).reshape(-1,1))
            
            features = prot_voxels.reshape(N[0], N[1], N[2], prot_voxels.shape[1])
            annotations = annotation_voxels.reshape(N[0], N[1], N[2], annotation_voxels.shape[1])
            
            with open(f'data/voxel-features/{pdb_id.lower()}{chain_id.upper()}.npy', 'wb') as f:
                np.save(f, features)
            with open(f'data/voxel-annotations/{pdb_id.lower()}{chain_id.upper()}.npy', 'wb') as f:
                np.save(f, annotations)

3QOV


2024-04-24 10:23:02,564 - moleculekit.molecule - WARNING - Alternative atom locations detected. Only altloc A was kept. If you prefer to keep all use the keepaltloc="all" option when reading the file.
2024-04-24 10:23:02,568 - moleculekit.molecule - INFO - Removed 136 atoms. 14384 atoms remaining in the molecule.
2024-04-24 10:23:02,852 - moleculekit.molecule - INFO - Removed 10976 atoms. 3408 atoms remaining in the molecule.



---- Molecule chain report ----
Chain A:
    First residue: GLY     0  
    Final residue: ASN   434  
---- End of chain report ----



Multiple occupancies found: CA in GLU A 16.
Multiple occupancies found: CB in GLU A 16.
Multiple occupancies found: CG in GLU A 16.
Multiple occupancies found: CD in GLU A 16.
Multiple occupancies found: OE1 in GLU A 16.
Multiple occupancies found: OE2 in GLU A 16.
Multiple occupancies found in GLU A 16. At least one of the instances is being ignored.
Multiple occupancies found: CA in GLU A 41.
Multiple occupancies found: CB in GLU A 41.
Multiple occupancies found: CG in GLU A 41.
Multiple occupancies found: CD in GLU A 41.
Multiple occupancies found: OE1 in GLU A 41.
Multiple occupancies found: OE2 in GLU A 41.
Multiple occupancies found in GLU A 41. At least one of the instances is being ignored.
Multiple occupancies found: CA in ARG A 85.
Multiple occupancies found: CB in ARG A 85.
Multiple occupancies found: CG in ARG A 85.
Multiple occupancies found: CD in ARG A 85.
Multiple occupancies found: NE in ARG A 85.
Multiple occupancies found: CZ in ARG A 85.
Multiple occupancies found: 

*** Open Babel Warning  in PerceiveBondOrders
  Failed to kekulize aromatic bonds in OBMol::PerceiveBondOrders (title is /tmp/tmpl_zwl1m4.pdb)


In [1]:
finished_pockets = {'2b9hA': ['BS02'], '2fnaA': ['BS01'], '1hi5A': ['BS01'], '3kjiA': ['BS02'], '1k3cA': ['BS01'], '3llmA': ['BS02'], '1nvaA': ['BS02'], '1pkgA': ['BS02'], '3nbxX': ['BS01'], '3ko5A': ['BS01'], '1fwkA': ['BS01'], '2dcnA': ['BS02'], '2axnA': ['BS03'], '3g2fA': ['BS01'], '1cnfA': ['BS02']}

In [2]:
import csv
import numpy as np
import os
from moleculekit.tools.atomtyper import metal_atypes
from moleculekit.molecule import Molecule
from moleculekit.tools.voxeldescriptors import getVoxelDescriptors
from moleculekit.tools.atomtyper import prepareProteinForAtomtyping

for file in ['data/ADP_Training.txt', 'data/ADP_Test.txt']:
    with open(file, newline='') as csvfile:
        
        reader = csv.reader(csvfile, delimiter=';')

        for row in reader:
            pdb_id = row[0]
            chain_id = row[1]
            pocket = row[2]

            id = pdb_id.lower() + chain_id.upper()

            if id in finished_pockets and pocket in finished_pockets[id]:
                continue

            print(pdb_id)
            binding_residues = [residue[1:] for residue in row[4].split(' ')]

            # selection query of the binding residues
            binding_residues_query = f'resid {" or resid ".join(binding_residues)}'

            if pdb_id == '3N3O':
                prot = Molecule('5SXR', validateElements=False)
            elif pdb_id == '1WE3':
                prot = Molecule('4V4O', validateElements=False)
            elif pdb_id == '3BFN':
                prot = Molecule('6NJE', validateElements=False)
            elif pdb_id == '3RBO':
                prot = Molecule('4JJZ', validateElements=False)
            elif pdb_id == '3QOV':
                prot = Molecule('4RVN', validateElements=False)
            else:
                prot = Molecule(pdb_id, validateElements=False)

            prot.filter(f'chain {chain_id} and protein')
            prot = prepareProteinForAtomtyping(prot)
            prot.filter(f"protein or water or element {' '.join(metal_atypes)}")

            annotation_voxels, _, N = getVoxelDescriptors(prot, buffer=8, userchannels=prot.atomselect(binding_residues_query).reshape(-1,1))
            annotations = annotation_voxels.reshape(N[0], N[1], N[2], annotation_voxels.shape[1])
            
            other_annotations_for_concatenation = None
            if os.path.isfile(f'data/voxel-annotations/{pdb_id.lower()}{chain_id.upper()}.npy'):
                other_annotations_for_concatenation = np.load(f'data/voxel-annotations/{pdb_id.lower()}{chain_id.upper()}.npy')

            with open(f'data/voxel-annotations/{id}.npy', 'wb') as f:
                if other_annotations_for_concatenation is not None:
                    annotations = annotations | other_annotations_for_concatenation
                np.save(f, annotations)
            
            if id not in finished_pockets:
                finished_pockets[id] = []
            finished_pockets[id].append(pocket)

2AWN


2024-04-24 14:48:47,335 - moleculekit.molecule - INFO - Removed 8135 atoms. 2534 atoms remaining in the molecule.
2024-04-24 14:48:47,492 - moleculekit.molecule - INFO - Removed 15 atoms. 2519 atoms remaining in the molecule.
2024-04-24 14:48:48,014 - numexpr.utils - INFO - NumExpr defaulting to 8 threads.



---- Molecule chain report ----
Chain A:
    First residue: ALA     2  
    Final residue: SER   373  
---- End of chain report ----



2024-04-24 14:48:50,211 - pdb2pqr.biomolecule - WARNING - Gap in backbone detected between LEU A 86 and GLU A 108!
2024-04-24 14:48:50,213 - pdb2pqr.biomolecule - WARNING - Gap in backbone detected between LEU A 121 and ALA A 143!
2024-04-24 14:48:50,219 - pdb2pqr.biomolecule - WARNING - Gap in backbone detected between ASP A 297 and LEU A 300!
2024-04-24 14:48:50,225 - pdb2pqr.biomolecule - WARNING - Missing atom CG in residue GLU A 119
2024-04-24 14:48:50,227 - pdb2pqr.biomolecule - WARNING - Missing atom CD in residue GLU A 119
2024-04-24 14:48:50,228 - pdb2pqr.biomolecule - WARNING - Missing atom OE1 in residue GLU A 119
2024-04-24 14:48:50,229 - pdb2pqr.biomolecule - WARNING - Missing atom OE2 in residue GLU A 119
2024-04-24 14:48:50,233 - pdb2pqr.biomolecule - WARNING - Missing atom CG in residue GLU A 257
2024-04-24 14:48:50,234 - pdb2pqr.biomolecule - WARNING - Missing atom CD in residue GLU A 257
2024-04-24 14:48:50,236 - pdb2pqr.biomolecule - WARNING - Missing atom OE1 in res

2QB5


...

1A9X


2024-04-24 14:55:06,112 - moleculekit.molecule - WARNING - Alternative atom locations detected. Only altloc A was kept. If you prefer to keep all use the keepaltloc="all" option when reading the file.
2024-04-24 14:55:06,123 - moleculekit.molecule - INFO - Removed 99 atoms. 49211 atoms remaining in the molecule.
2024-04-24 14:55:06,894 - moleculekit.molecule - INFO - Removed 41042 atoms. 8169 atoms remaining in the molecule.
2024-04-24 14:55:07,547 - moleculekit.tools.preparation - WARNING - Both chains and segments are defined in Molecule.chain / Molecule.segid, however they are inconsistent. Protein preparation will use the chain information.



---- Molecule chain report ----
Chain A:
    First residue: MET     1  
    Final residue: ORN  1920  
---- End of chain report ----



Multiple occupancies found: CB in ARG A 490.
Multiple occupancies found: CG in ARG A 490.
Multiple occupancies found: CD in ARG A 490.
Multiple occupancies found: NE in ARG A 490.
Multiple occupancies found: CZ in ARG A 490.
Multiple occupancies found: NH1 in ARG A 490.
Multiple occupancies found: NH2 in ARG A 490.
Multiple occupancies found in ARG A 490. At least one of the instances is being ignored.
Multiple occupancies found: CB in ASP A 518.
Multiple occupancies found: CG in ASP A 518.
Multiple occupancies found: OD1 in ASP A 518.
Multiple occupancies found: OD2 in ASP A 518.
Multiple occupancies found in ASP A 518. At least one of the instances is being ignored.
Multiple occupancies found: CB in ASN A 554.
Multiple occupancies found: CG in ASN A 554.
Multiple occupancies found: OD1 in ASN A 554.
Multiple occupancies found: ND2 in ASN A 554.
Multiple occupancies found in ASN A 554. At least one of the instances is being ignored.
Multiple occupancies found: CB in MET A 772.
Multipl

TypeError: ufunc 'bitwise_or' not supported for the input types, and the inputs could not be safely coerced to any supported types according to the casting rule ''safe''

In [5]:
print(finished_pockets)

{'2b9hA': ['BS02'], '2fnaA': ['BS01'], '1hi5A': ['BS01'], '3kjiA': ['BS02'], '1k3cA': ['BS01'], '3llmA': ['BS02'], '1nvaA': ['BS02'], '1pkgA': ['BS02'], '3nbxX': ['BS01'], '3ko5A': ['BS01'], '1fwkA': ['BS01'], '2dcnA': ['BS02'], '2axnA': ['BS03'], '3g2fA': ['BS01'], '1cnfA': ['BS02']}
